In [1]:
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from typing import List, Dict
from tqdm import tqdm
import re
import numpy as np
import os
from datetime import datetime
from tabulate import tabulate
import json

class RecipeEvaluator:
    def __init__(self, device: str = None):
        self.device = device if device else ('cuda' if torch.cuda.is_available() else 'cpu')
        print(f"Using device: {self.device}")
        
        print("Loading tokenizer...")
        self.tokenizer = AutoTokenizer.from_pretrained(
            "Qwen/Qwen2.5-7B-Instruct", 
            trust_remote_code=True
        )
        self.tokenizer.pad_token = self.tokenizer.eos_token
        
        print("Loading model...")
        model_kwargs = {
            "trust_remote_code": True,
            "torch_dtype": torch.float16 if self.device == 'cuda' else torch.float32,
        }
        
        if self.device == 'cuda':
            model_kwargs["device_map"] = "auto"
        
        try:
            self.model = AutoModelForCausalLM.from_pretrained(
                "Qwen/Qwen2.5-7B-Instruct",
                **model_kwargs
            )
        except Exception as e:
            print(f"Error loading model: {e}")
            raise

    def create_prompt(self, recipe_name: str, ingredients: str, generation: str, allergens: List[str] = None) -> str:
        allergen_text = f"\nAllergens: {', '.join(allergens)}" if allergens else "\nAllergens: None specified"
        
        prompt = f"""Evaluate this recipe with scores from 1-5:

Recipe Name: {recipe_name}
Ingredients: {ingredients}{allergen_text}
Instructions:
{generation}

Rate each aspect (1 is lowest, 5 is highest):
### Clarity: [score]/5
[clarity explanation]
  
### Completeness: [score]/5
[completeness explanation]
  
### Consistency: [score]/5
[consistency explanation]
  
### Practicality: [score]/5
[practicality explanation]
  
### Relevance: [score]/5
[relevance explanation]

### Allergen Safety: [score]/5
[evaluate if the recipe properly handles/warns about allergens present in ingredients]"""
        return prompt

    def parse_evaluation(self, response: str) -> Dict:
        print("\nDEBUG - Raw response:")
        print(response)
        print("\nAttempting to parse...")
        
        metrics = {
            'clarity': None,
            'completeness': None,
            'consistency': None,
            'practicality': None,
            'relevance': None,
            'allergen_safety': None,
            'explanation': ''
        }
        
        try:
            patterns = [
                r'\*\*Score:?\*\*:?\s*(\d+)(?:/5|\s*out\s*of\s*5)',  # Matches **Score:** X/5 or X out of 5
                r'(?:Clarity|Completeness|Consistency|Practicality|Relevance|Allergen Safety):?\s*(?:\*\*)?(\d+)(?:/5|\s*out\s*of\s*5)',  # Matches Metric: X/5
                r'(?:Clarity|Completeness|Consistency|Practicality|Relevance|Allergen Safety).*?:\s*(\d+)(?:/5|\s*out\s*of\s*5)',  # Matches description followed by X/5
                r'\*\*(\d+)\*\*\s*(?:/|\s*out\s*of\s*)5',  # Matches **X** /5 or out of 5
                r'Score:\s*(\d+)(?:/5|\s*out\s*of\s*5)',  # Matches Score: X/5
                r'(\d+)/5',  # Simple X/5 format
                r'\*\*Score:\s*(\d+)\*\*',  # Matches **Score: X**
                r'\*\*Clarity\*\*:\s*(\d+)',  # Matches **Metric**: X
                r'- \*\*(?:Clarity|Completeness|Consistency|Practicality|Relevance|Allergen Safety)\*\*:\s*(\d+)\s*/\s*5'  # Matches - **Metric**: X / 5
            ]
            

            sections = re.split(r'(?:###?|####)\s+(?:\*\*)?', response)
            
            for section in sections:
                section = section.strip()
                for metric in metrics.keys():
                    metric_name = metric.replace('_', ' ').lower()
                    if metric != 'explanation' and metric_name in section.lower():
                        for pattern in patterns:
                            match = re.search(pattern, section, re.IGNORECASE | re.MULTILINE)
                            if match:
                                try:
                                    score = int(match.group(1))
                                    if 1 <= score <= 5:
                                        metrics[metric] = score
                                        explanation = re.sub(r'\*\*.*?\*\*|\d+/5|\d+\s*out\s*of\s*5', '', section).strip()
                                        if explanation:
                                            metrics['explanation'] += f"{metric.capitalize()}: {explanation}\n"
                                        break
                                except ValueError:
                                    continue
            

            if any(v is None for v in metrics.values() if isinstance(v, (int, float)) or v is None):
                for metric in metrics.keys():
                    if metric != 'explanation' and metrics[metric] is None:
                        metric_name = metric.replace('_', ' ')
                        score_pattern = fr'{metric_name}.*?(\d+)(?:/5|\s*out\s*of\s*5)'
                        match = re.search(score_pattern, response, re.IGNORECASE | re.MULTILINE)
                        if match:
                            try:
                                score = int(match.group(1))
                                if 1 <= score <= 5:
                                    metrics[metric] = score
                            except ValueError:
                                continue
            
            metrics['explanation'] = metrics['explanation'].strip()
            

            if all(metrics[k] is not None for k in metrics.keys() if k != 'explanation'):
                print("Successfully parsed scores:", metrics)
                return metrics
            else:
                missing = [k for k, v in metrics.items() if v is None and k != 'explanation']
                print(f"Missing values for: {missing}")
                if any(metrics[k] is not None for k in metrics.keys() if k != 'explanation'):
                    return metrics
                return None

        except Exception as e:
            print(f"Error parsing evaluation: {e}")
            print("Raw response:", response)
            return None

    def evaluate_recipe(self, recipe_name: str, ingredients: str, generation: str, allergens: List[str] = None) -> Dict:
        prompt = self.create_prompt(recipe_name, ingredients, generation, allergens)
        
        print(f"\nEvaluating recipe: {recipe_name}")
        
        try:
            inputs = self.tokenizer(prompt, return_tensors="pt")
            if self.device == 'cuda':
                inputs = inputs.to(self.device)
            
            with torch.no_grad():
                outputs = self.model.generate(
                    **inputs,
                    max_new_tokens=512,
                    do_sample=False,
                    num_return_sequences=1,
                    pad_token_id=self.tokenizer.eos_token_id,
                    eos_token_id=self.tokenizer.eos_token_id,
                    repetition_penalty=1.2
                )
            
            response = self.tokenizer.decode(outputs[0], skip_special_tokens=True)
            response = response.replace(prompt, "").strip()
            
            evaluation = self.parse_evaluation(response)
            if evaluation:
                evaluation['recipe_name'] = recipe_name
                return evaluation
            return None
            
        except Exception as e:
            print(f"Error generating evaluation: {e}")
            return None

    def evaluate_model_outputs(self, model_outputs: List[Dict], model_type: str = "unnamed") -> pd.DataFrame:
        """Evaluate a batch of model outputs using the LLM judge"""
        results = []
        
        for output in tqdm(model_outputs, desc=f"Evaluating {model_type} outputs"):
            evaluation = self.evaluate_recipe(
                output['name'],
                output['ingredients'],
                output['generation'],
                output.get('allergens', ['milk','eggs','fish'])
            )
            if evaluation:
                evaluation['model_type'] = model_type
                results.append(evaluation)
        
        return pd.DataFrame(results)

    def save_evaluation_results(self, baseline_results: pd.DataFrame, finetuned_results: pd.DataFrame, 
                              output_dir: str = "evaluation_results"):
        """Save evaluation results and generate visualizations"""
        os.makedirs(output_dir, exist_ok=True)
        timestamp = datetime.now().strftime('%Y%m%d_%H%M%S')
        

        baseline_results.to_csv(f"{output_dir}/baseline_results_{timestamp}.csv", index=False)
        finetuned_results.to_csv(f"{output_dir}/finetuned_results_{timestamp}.csv", index=False)
        

        metrics_cols = ['clarity', 'completeness', 'consistency', 'practicality', 'relevance', 'allergen_safety']
        baseline_avg = baseline_results[metrics_cols].mean()
        finetuned_avg = finetuned_results[metrics_cols].mean()
        

        self.create_comparison_radar(baseline_avg, finetuned_avg, 
                                   f"{output_dir}/model_comparison_{timestamp}.png")
        

        self.generate_summary_report(baseline_avg, finetuned_avg, 
                                   f"{output_dir}/evaluation_summary_{timestamp}.md")

    def create_comparison_radar(self, baseline_metrics: pd.Series, finetuned_metrics: pd.Series, 
                              output_path: str):
        """Create a radar chart comparing baseline and finetuned models"""
        metrics = baseline_metrics.index
        angles = np.linspace(0, 2*np.pi, len(metrics), endpoint=False)
        angles = np.concatenate((angles, [angles[0]]))
        
        fig, ax = plt.subplots(figsize=(10, 10), subplot_kw=dict(projection='polar'))
        

        values = np.concatenate((baseline_metrics.values, [baseline_metrics.values[0]]))
        ax.plot(angles, values, 'o-', linewidth=2, label='Baseline')
        ax.fill(angles, values, alpha=0.25)
        

        values = np.concatenate((finetuned_metrics.values, [finetuned_metrics.values[0]]))
        ax.plot(angles, values, 'o-', linewidth=2, label='Fine-tuned')
        ax.fill(angles, values, alpha=0.25)
        
        ax.set_theta_offset(np.pi / 2)
        ax.set_theta_direction(-1)
        ax.set_xticks(angles[:-1])
        ax.set_xticklabels(metrics)
        ax.set_ylim(0, 5)
        
        plt.title("Model Comparison\nAverage Evaluation Metrics", pad=20)
        plt.legend(loc='center left', bbox_to_anchor=(1.2, 0.5))
        
        plt.savefig(output_path, bbox_inches='tight', dpi=300)
        plt.close()

    def generate_summary_report(self, baseline_metrics: pd.Series, finetuned_metrics: pd.Series, 
                              output_path: str):
        """Generate a markdown report summarizing the evaluation results"""
        with open(output_path, 'w') as f:
            f.write("# Model Evaluation Summary\n\n")
            f.write(f"Generated on: {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}\n\n")
            
            f.write("## Average Metrics Comparison\n\n")
            comparison_data = []
            for metric in baseline_metrics.index:
                baseline = baseline_metrics[metric]
                finetuned = finetuned_metrics[metric]
                improvement = finetuned - baseline
                pct_change = (improvement / baseline) * 100 if baseline != 0 else float('inf')
                
                comparison_data.append([
                    metric,
                    f"{baseline:.3f}",
                    f"{finetuned:.3f}",
                    f"{improvement:+.3f}",
                    f"{pct_change:+.1f}%"
                ])
            
            headers = ["Metric", "Baseline", "Fine-tuned", "Improvement", "% Change"]
            f.write(tabulate(comparison_data, headers=headers, tablefmt="pipe"))
            f.write("\n\n")

def load_model_outputs(json_path: str) -> List[Dict]:
    """Load model outputs from a JSON file"""
    try:
        with open(json_path, 'r', encoding='utf-8') as f:
            outputs = json.load(f)
        print(f"Loaded {len(outputs)} outputs from {json_path}")
        return outputs
    except Exception as e:
        print(f"Error loading outputs from {json_path}: {e}")
        raise

def main():
    try:
        print("Initializing evaluator...")
        evaluator = RecipeEvaluator()
        

        baseline_outputs = load_model_outputs("smollm360_generated_recipes_500.json")
        finetuned_outputs = load_model_outputs("smollm360_generated_finetuned_recipes_500.json")
        
        print("\nEvaluating baseline outputs...")
        baseline_results = evaluator.evaluate_model_outputs(baseline_outputs, "baseline")
        
        print("\nEvaluating finetuned outputs...")
        finetuned_results = evaluator.evaluate_model_outputs(finetuned_outputs, "finetuned")
        
        print("\nSaving results and generating visualizations...")
        evaluator.save_evaluation_results(baseline_results, finetuned_results)
        
        print("\nEvaluation complete!")
        
    except Exception as e:
        print(f"An error occurred: {e}")
        raise

if __name__ == "__main__":
    main()

Initializing evaluator...
Using device: cuda
Loading tokenizer...
Loading model...


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Loaded 500 outputs from smollm360_generated_recipes_500.json
Loaded 500 outputs from smollm360_generated_finetuned_recipes_500.json

Evaluating baseline outputs...


Evaluating baseline outputs:   0%|          | 0/500 [00:00<?, ?it/s]


Evaluating recipe: cottage cheese waffles


...

Evaluating finetuned outputs: 100%|█████████▉| 499/500 [2:03:42<00:14, 14.92s/it]


DEBUG - Raw response:
### Evaluation of Recipe "Catfish or Any Firm White Fish with Pecan Sauce"

#### Clarity: **2/5**
The instructions are vague and do not provide clear steps on how to prepare the dish. The name suggests a simple pecan-based sauce for catfish but does not specify what kind of preparation method should be used.

#### Completeness: **3/5**
While it lists some necessary ingredients like catfish fillets, pecans, and seasonings, there's no detailed list provided that would help someone replicate the recipe accurately. Additionally, key details such as cooking times, temperatures, and specific measurements are missing.

#### Consistency: **2/5**
There seems to be an inconsistency between the two sections of the recipe. One part describes making a pecan sauce for catfish while another section provides a long list of unrelated spices and condiments without context. This makes it difficult to follow either set of directions coherently.

#### Practicality: **2/5**
Due to its

Evaluating finetuned outputs: 100%|██████████| 500/500 [2:03:56<00:00, 14.87s/it]


DEBUG - Raw response:
### Evaluation of "Rosemary Polenta Pound Cake" Recipe

#### Clarity: **2/5**
The name and instructions provided are confusing. The title mentions a combination that doesn't align well ("roselle," which isn’t mentioned again) or make sense together as it stands. Additionally, there's no clear indication what type of dish we're making—whether it’s actually a pound cake or something else entirely.

#### Completeness: **3/5**
While most basic components for a pound cake are listed (butter, sugar, eggs), other essential elements like leavening agents (yeast instead of baking powder/soda) aren't included. There seems to be an inconsistency between mentioning “polenta” yet listing flour separately without specifying its role. 

#### Consistency: **2/5**
There appears to be significant confusion regarding ingredient lists and their roles. For instance, items such as "orange juice puree," "lemon peel zest," and various spices don't seem relevant to creating a traditional


Evaluation complete!
